# Graphs for the performance report

### Aircraft parameters

In [1]:
Max_g=3.17 #structural limit

In [ ]:
import libs
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.interpolate import griddata

matlab_template = dict(
        layout=go.Layout(
                #plot layout
                width=1300,
                height=800,
                showlegend=True,
                plot_bgcolor="white",
                margin=dict(t=200), #leave some padding on top

                #title
                title_font=dict(size=24, color="black", weight='bold',family="Arial",),
                title_x=0.5,  # Center the title horizontally
                title_y=0.98,  # Position the title slightly lower vertically

                #axis
                xaxis = dict(linecolor='black', showgrid=True, showline=True, gridcolor='lightgrey', ticks='outside', tickcolor='black', tickwidth=2, ticklen=5,
                             title_font=dict(size=18, weight='bold', family='Arial'),
                             tickfont=dict(size=14, family='Arial'),
                             ),
                yaxis = dict(linecolor='black', showgrid=True, showline=True, gridcolor='lightgrey', ticks='outside', tickcolor='black', tickwidth=2, ticklen=5,
                             title_font=dict(size=18, weight='bold', family='Arial'),
                             tickfont=dict(size=14, family='Arial'),
                             ),
                yaxis2 = dict(linecolor='black', showgrid=False, showline=True, gridcolor='lightgrey', ticks='outside', tickcolor='black', tickwidth=2, ticklen=5,
                             title_font=dict(size=18, weight='bold', family='Arial'),
                             tickfont=dict(size=14, family='Arial'),
                             ),

                #legend
                legend=dict(
                        x=1.1,                # Position the legend at the far-right of the plot
                        y=1.1,                # Position the legend at the top of the plot
                        xanchor='right',    # Anchor the legend on the right side
                        yanchor='bottom',      # Anchor the legend at the top
                        bordercolor='black',# Border color around the legend (optional)
                        borderwidth=1       # Border width around the legend (optional)
                        ),
         )
)

layout_Ps_contour=dict(
        title="C-12C Specific Excess power",
        xaxis=dict(title='True Airspeed (kt)', showgrid=True,range=[0,220]),  # Show gridlines on the x-axis
        yaxis=dict(showgrid=True, title='Altitude (ft)'),  # Show gridlines on the y-axis (for the first subplot)
        margin=dict(t=100), #leave some padding on top
)


## MOP1 MCP level excess power (1g)

### Level accel cruise configuration

In [3]:
#Data for level accel cruise configuration at 7000 ft
accel_data=pd.read_csv(r"data\Perf\master_level_accel_0flap.csv")
sawtooth_data=pd.read_csv(r"data\Perf\master_sawtooth.csv")
YAPS=True #True if the aircraft was in YAPS configuration, else False. Use for correcting the static pressure in the pitot-static system.
ID=[6] #ID of the level accels
sawtooth_ID=[4,5,10,11,12,16,17,18] #ID of the sawtooth data at 7k



In [ ]:
filtered_data=accel_data[accel_data['ID'].isin(ID)]
filtered_sawtooth_data=sawtooth_data[sawtooth_data['ID'].isin(sawtooth_ID)]

left_text="<b>Configuration:</b> Cruise<br><b>Power setting:</b> MCP<br><b>Temperature:</b> ISA<br><b>Altitude:</b> 7 000 ft<br>"
center_text="<b>Data basis:</b> Flight test<br><b>Test date:</b> April 25th, 2025<br><b>Tail number:</b> 73-01215<br><b>Weight:</b> 10 900 lb<br>"

fig=go.Figure()

fig = make_subplots(
    rows=2,
    cols=1,
    vertical_spacing=0.15,
    subplot_titles=("Specific energy height", "Specific Excess Power"),  # Titles for each subplot
    # Define a secondary y-axis for each subplot
    specs=[[{"secondary_y": True} for _ in range(1)] for _ in range(2)],
)

fig.update_layout(
    template=matlab_template,
    width=8.42*180,
    height=6.4*180,
    showlegend=False,
    title="C-12C Maximum Continuous Power Level Specific Excess Power",
    xaxis_title="Time (s)",
    xaxis=dict(range=[0, 80]),
    yaxis_title="Energy Height, Es (ft)",
    yaxis=dict(range=[7000, 11000],),
    xaxis2_title="True Airspeed, TAS (KTAS)",
    xaxis2=dict(range=[100, 260], showgrid=True),
    yaxis2_title="True airspeed, TAS (KTAS)",
    yaxis2=dict(range=[100, 260], color='blue',showgrid=True),
    yaxis3_title="Specific Excess Power (ft/sec)",
    yaxis3=dict(range=[0, 60], showgrid=True),
)



for id, group in filtered_data.groupby('ID'):
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['Es'], mode='markers', marker=dict(symbol='cross',size=7,color='black'),name=f'Data points {id}'),row=1, col=1)
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['TAS'], mode='lines', line=dict(color='blue')),secondary_y=True, row=1, col=1)
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['Es_fit'], line=dict(color='black')),row=1, col=1)

for id, group in filtered_data.groupby('ID'):
    # group['Ps_savgol']=signal.savgol_filter(group['Ps'],51,2)

    # fig2.add_trace(go.Scatter(x=group['TAS'], y=group['Ps'],yaxis='y', name=f'Data points {id}',mode='lines',line=dict(color='black',)))
    fig.add_trace(go.Scatter(x=group['TAS'], y=group['Ps_fit'],yaxis='y', mode='lines', name=f'Curve fitting {id}',line=dict(color='black',)),row=2, col=1)
    # fig2.add_trace(go.Scatter(x=group['TAS'], y=group['Ps_old'],yaxis='y', mode='lines', name=f'Curve fitting {id}',line=dict(color='red',)))

    # fig2.add_trace(go.Scatter(x=group['TAS'], y=group['Ps_savgol'],yaxis='y', name=f'Curve fitting',line=dict(color='black')))

fig.add_trace(go.Scatter(x=filtered_sawtooth_data['TAS'],y=filtered_sawtooth_data['Ps'],name='Sawtooth climbs', mode='markers',marker=dict(symbol='diamond-open',size=10,color='black',)),row=2, col=1)
fig.add_trace(go.Scatter(x=[libs.atm.CAStoTAS(160,7000,0,Offset=False)],y=[35],name='Requirement',mode='markers',marker=dict(symbol='x',size=10, color='black')),row=2, col=1)

for annotation in fig['layout']['annotations']:
    annotation['font'] = dict(size=20, weight='bold')  # Set desired font size for subplot titles


fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=left_text,
    showarrow=False,)

fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=center_text,
    showarrow=False,)

fig.show()


## Level accel power approach 7 000 ft

In [ ]:
#Data for power approch configuration at 7000 ft
accel_data=pd.read_csv(r"data\Perf\master_level_accel_40flap.csv")
sawtooth_data=pd.read_csv(r"data\Perf\master_sawtooth.csv")

left_text="<b>Configuration:</b> Approach (Flaps 40%, gear down)<br><b>Power setting:</b> MCP<br><b>Temperature:</b> ISA+10<br><b>Altitude:</b> 7 000 ft<br>"
center_text="<b>Data basis:</b> Flight test<br><b>Test date:</b> April 22th, 2025<br><b>Tail number:</b> 76-00158<br><b>Weight:</b> 11 800 lb<br>"

ID=[3] #ID of the level accels in power approach at 7000ft

filtered_data=accel_data[accel_data['ID'].isin(ID)]

fig=go.Figure()

fig = make_subplots(
    rows=2,
    cols=1,
    vertical_spacing=0.15,
    subplot_titles=("Specific energy height", "Specific Excess Power"),  # Titles for each subplot
    # Define a secondary y-axis for each subplot
    specs=[[{"secondary_y": True} for _ in range(1)] for _ in range(2)],
)

fig.update_layout(
    template=matlab_template,
    width=8.42*180,
    height=6.4*180,
    showlegend=False,
    title="C-12C Maximum Continuous Power Level Specific Excess Power",
    xaxis_title="Time (s)",
    xaxis=dict(range=[0, 40]),
    yaxis_title="Energy Height, Es (ft)",
    yaxis=dict(range=[7000, 9500],),
    xaxis2_title="True Airspeed, TAS (KTAS)",
    xaxis2=dict(range=[100, 200], showgrid=True),
    yaxis2_title="True airspeed, TAS (KTAS)",
    yaxis2=dict(range=[100, 200], color='blue',showgrid=True),
    yaxis3_title="Specific Excess Power (ft/sec)",
    yaxis3=dict(range=[0, 60], showgrid=True),
)



for id, group in filtered_data.groupby('ID'):
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['Es'], mode='markers', marker=dict(symbol='cross',size=7,color='black'),name=f'Data points {id}'),row=1, col=1)
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['TAS'], mode='lines', line=dict(color='blue')),secondary_y=True, row=1, col=1)
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['Es_fit'], line=dict(color='black')),row=1, col=1)

for id, group in filtered_data.groupby('ID'):
    # group['Ps_savgol']=signal.savgol_filter(group['Ps'],51,2)

    # fig2.add_trace(go.Scatter(x=group['TAS'], y=group['Ps'],yaxis='y', name=f'Data points {id}',mode='lines',line=dict(color='black',)))
    fig.add_trace(go.Scatter(x=group['TAS'], y=group['Ps_fit'],yaxis='y', mode='lines', name=f'Curve fitting {id}',line=dict(color='black',)),row=2, col=1)
    # fig2.add_trace(go.Scatter(x=group['TAS'], y=group['Ps_old'],yaxis='y', mode='lines', name=f'Curve fitting {id}',line=dict(color='red',)))

    # fig2.add_trace(go.Scatter(x=group['TAS'], y=group['Ps_savgol'],yaxis='y', name=f'Curve fitting',line=dict(color='black')))

fig.add_trace(go.Scatter(x=[libs.atm.CAStoTAS(125,7000,0,Offset=False)],y=[22],name='Requirement',mode='markers',marker=dict(symbol='x',size=10, color='black')),row=2, col=1)

for annotation in fig['layout']['annotations']:
    annotation['font'] = dict(size=20, weight='bold')  # Set desired font size for subplot titles


fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=left_text,
    showarrow=False,)

fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=center_text,
    showarrow=False,)

fig.show()


## MOP2 climb schedule

In [ ]:
#Data SEP contour plot
accel_data=pd.read_csv(r"data\Perf\master_level_accel_0flap.csv")

left_text="<b>Configuration:</b> Cruise<br><b>Power setting:</b> MCP<br><b>Temperature:</b> Test day<br>"
center_text="<b>Data basis:</b> Flight test<br><b>Test date:</b> April 8th, 2025 to May 25th, 2025<br><b>Tail number:</b> 73-01215 and 76-00158<br>"

In [ ]:
fig=go.Figure()

accel_data['FL']= ((accel_data['BARO_ALT'] / 500).round()*5 ).astype(int) #rescale to similar than speed
accel_data['TAS_rounded']= accel_data['TAS'].round().astype(int)

x=np.linspace(100, 280, 181)
y=np.linspace(70, 200, 27)
X, Y = np.meshgrid(x, y)
z = np.full((len(y), len(x)), np.nan)  # initialize with NaNs
for i in range(len(y)):
    for j in range(len(x)):
        z[i,j]=accel_data.loc[(accel_data['FL']==y[i]) & (accel_data['TAS_rounded']==x[j]),'Ps_fit'].mean()


# 1️⃣ Interpolate missing (NaN) values using griddata
# Step 1: Get known points
x_known, y_known = np.meshgrid(x, y)
points_known = np.column_stack((x_known[~np.isnan(z)], y_known[~np.isnan(z)]))
values_known = z[~np.isnan(z)]

# Step 2: Create full grid
points_full = np.column_stack((X.ravel(), Y.ravel()))

# Step 3: Interpolate
z_interp = griddata(points_known, values_known, points_full, method='cubic',rescale=True)
z_interp = z_interp.reshape(z.shape)

# 2️⃣ Optional: Smooth the result using Gaussian filter
# z_smooth = gaussian_filter(z_interp, sigma=1)

fig.add_trace(go.Contour(
    x=x,
    y=y*100,
    z=z_interp,
    colorscale='YlOrRd',
    colorbar=dict(title='Specific Excess Power (ft/s)', thickness=20, tickfont=dict(size=14, family='Arial')),
    line=dict(color='black',width=2),
    contours=dict(
        showlines=True,
        showlabels=True,
        labelfont=dict(size=16,color='black',weight='bold'),
        start=0,
        size=10,
        end=60,
        ),
    contours_coloring='none',
    ))

x=np.linspace(0, 280, 281)
y=np.zeros(len(x))

#plot energy height lines
for i in range(0,25000,2000):
    for j in range(len(x)):
        y[j]=i-1/(2*32.2)*(libs.atm.CAStoTAS(x[j],i,0,Offset=True)*1.68781)**2

    if i%10000==0:
        dash='dash'
        width=1
    else:
        dash='dash'
        width=1
    fig.add_trace(go.Scatter(x=x,y=y,line=dict(dash=dash, color='black', width=width)))

fig.update_layout(template=matlab_template,
        title="C-12C Climb Schedule",
        xaxis=dict(title='Calibrated Airspeed (kt)',range=[100,260]),
        yaxis=dict(title='Pressure Altitude (ft)', range=[7000,20000]),
        showlegend=False,
        width=8.42*180,
        height=6.4*180,
        )

fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=left_text,
    showarrow=False,)

fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=center_text,
    showarrow=False,)


fig.show()

## MOP3 Flight manual cruise Climb

In [ ]:
#Data for cruise climb
climb_data=pd.read_csv(r"data\Perf\master_cruise_climb.csv")

ID=[0] #ID of the level accels in manual cruise climb from 5000 to 20000ft

#Flight manual data (to be updated based on the day conditions, mostly temperature)
Time_to_climb_20k=10*60-2*60 #in seconds (for ISA conditions and 11000 lb, 6.3 min to climb from 5000 to 20000ft)
Fuel_to_climb_20k=135-25 #in lb (for ISA conditions and 11000 lb, 100 lb to climb from 5000 to 20000ft)
Distance_to_climb_20k=28-5 #in nm (for ISA conditions and 11000 lb, 19 nm to climb from 5000 to 20000ft)

left_text="<b>Configuration:</b> Cruise<br><b>Calibrated airspeed:</b> 160 KIAS then 140 KIAS above 10,000 ft<br><b>Power setting:</b> MCP<br><b>Weight:</b> 12,500 lb<br>"
center_text="<b>Data basis:</b> Flight test<br><b>Test date:</b> April 8th, 2025<br><b>Tail number:</b> 73-01215<br><b>Temperature:</b> ISA+5°C<br>"

In [ ]:
filtered_data=climb_data[climb_data['ID'].isin(ID)]

fig=go.Figure()

fig = make_subplots(
    rows=3,
    cols=1,
    shared_xaxes=False,  # Optional: you can customize axes sharing
    shared_yaxes=False,  # We will be using individual y-axes for each plot
    vertical_spacing=0.15,
    subplot_titles=("Time to climb", "Fuel to climb", "Distance to climb"),  # Titles for each subplot
    # Define a secondary y-axis for each subplot
)

fig.update_layout(
    template=matlab_template,
    width=8.42*180,
    height=6.4*180,
    showlegend=False,
    title="C-12C Climb cruise (5000 to 20000 ft)",
    xaxis_title="Time (s)",
    xaxis=dict(range=[0, 605]),
    xaxis2_title="Fuel (lb)",
    xaxis3_title="Distance (Nm)",
    yaxis_title="Altitude (ft)",
    yaxis=dict(range=[0, 21000]),
    yaxis2_title="Altitude (ft)",
    yaxis2=dict(range=[0, 21000], showgrid=True),
    yaxis3_title="Altitude (ft)",
    yaxis3=dict(range=[0, 21000]),
)

for id, group in filtered_data.groupby('ID'):
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black')),row=1, col=1)
    fig.add_trace(go.Scatter(x=group['Fuel'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black')),row=2, col=1)
    fig.add_trace(go.Scatter(x=group['Distance'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black')),row=3, col=1)

#Plot flight manual data
#Altitude
fig.add_trace(go.Scatter(x=[0,Time_to_climb_20k], y=[5000,20000],name="Flight manual",mode='lines+text',line=dict(color='black', dash='dash')), row=1, col=1)
fig.add_trace(go.Scatter(x=[0,Time_to_climb_20k*0.9], y=[5000,20000],name='+/-10%',mode='lines',line=dict(color='black', dash='dot')), row=1, col=1)
fig.add_trace(go.Scatter(x=[0,Time_to_climb_20k*1.1], y=[5000,20000],name='+10%', mode='lines',line=dict(color='black', dash='dot'), showlegend=False), row=1, col=1)

#Fuel
fig.add_trace(go.Scatter(x=[0,Fuel_to_climb_20k], y=[5000,20000],name="Flight manual",mode='lines',line=dict(color='black', dash='dash'), showlegend=False), row=2, col=1)
fig.add_trace(go.Scatter(x=[0,Fuel_to_climb_20k*0.9], y=[5000,20000],name='-10%',mode='lines',line=dict(color='black', dash='dot'), showlegend=False), row=2, col=1)
fig.add_trace(go.Scatter(x=[0,Fuel_to_climb_20k*1.1], y=[5000,20000],name='+10%',mode='lines',line=dict(color='black', dash='dot'), showlegend=False), row=2, col=1)

#Distance
fig.add_trace(go.Scatter(x=[0,Distance_to_climb_20k], y=[5000,20000],name="Flight manual", mode='lines',line=dict(color='black', dash='dash'), showlegend=False), row=3, col=1)
fig.add_trace(go.Scatter(x=[0,Distance_to_climb_20k*0.9], y=[5000,20000],name='-10%', mode='lines',line=dict(color='black', dash='dot'), showlegend=False),row=3, col=1)
fig.add_trace(go.Scatter(x=[0,Distance_to_climb_20k*1.1], y=[5000,20000],name='+10%',mode='lines',line=dict(color='black', dash='dot'), showlegend=False),row=3, col=1)

#Plot requirement
fig.add_trace(go.Scatter(x=[600], y=[20000],yaxis='y',mode='markers',name='Requirement',marker=dict(color='black',symbol='x',size=10)),row=1,col=1)

for annotation in fig['layout']['annotations']:
    annotation['font'] = dict(size=20, weight='bold')  # Set desired font size her

fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=left_text,
    showarrow=False,)

fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=center_text,
    showarrow=False,)



fig.show()
fig.write_image("data/Perf/Cruise_climb.png", engine='kaleido')

## MOP4 MCP Level Sustained Turn

In [10]:
#Data for level sustained turn
turn_data=pd.read_csv(r"data\Perf\master_level_turn.csv")
Vstall=100  #stall speeds for graph



In [ ]:
for group in turn_data.groupby('CATEGORY'):
    group_altitude=group['CATEGORY'].iloc[0]
    Vstall_TAS=libs.atm.CAStoTAS(Vstall,group_altitude,0,Offset=True)  #get the 1.1 Vstall at that altitude in TAS
    Vmo=libs.atm.CAStoTAS(259,group_altitude)
    Test_date={'5000':'April 17th, 2025','10000':'April 17th, 2025','15000':'April 18th, 2025','20000':'April 18th, 2025',} #Test date

    left_text=f"<b>Configuration:</b> Cruise<br><b>Altitude:</b> {round(group_altitude):,} ft<br><b>Power setting:</b> MCP<br>"
    center_text=f"<b>Data basis:</b> Flight test<br><b>Test date:</b> {Test_date[str(group_altitude)]}<br><b>Tail number:</b> 76-00158<br>"

    fig=go.Figure()
    fig.update_layout(
        template=matlab_template,
        title="C-12C Level turn ("+str(round(group_altitude))+' ft)',
        xaxis=dict(title='True Airspeed (kt)',range=[100,Vmo+10]),
        yaxis=dict(title='Turn rate (°/sec)'),
        legend=dict(x=0.95, y=0.95,),
        width=8.42*180,
        height=6.4*180,
    )

    #Calculate the load factor and turn radius for the contour plot
    x=np.linspace(100, Vmo, 301)
    y=np.linspace(0.5, 20, 80)
    TAS,TURN_RATE=np.meshgrid(x,y)
    Nz=np.sqrt(((np.deg2rad(TURN_RATE)*TAS*libs.cst.KT_TO_FPS)/libs.cst.G_IMPERIAL)**2+1) #Load factor in g
    TURN_RADIUS=(TAS*libs.cst.KT_TO_FPS)/np.deg2rad(TURN_RATE) #Turn radius in ft

    #compute the Vstall as function of the G
    Vstall_alt=libs.atm.CAStoTAS(Vstall,group_altitude,0,Offset=True)
    Vstall_maxg=Vstall_alt*np.sqrt(Max_g)
    Vstall_vect=np.linspace(Vstall_alt,Vstall_maxg,150)
    Omega_vect=np.rad2deg(libs.cst.G_IMPERIAL/(Vstall_vect*libs.cst.KT_TO_FPS)*np.sqrt((Vstall_vect/Vstall_alt)**4-1))
    Omega_Vmo=np.rad2deg(libs.cst.G_IMPERIAL/(Vmo*libs.cst.KT_TO_FPS)*np.sqrt((Max_g)**2-1))

    #plot the level turns
    fig.add_trace(go.Scatter(
        x=group['TAS'],y=group['TURN_RATE'],
        name='Level turns', mode='markers',
        marker=dict(symbol='diamond-dot',size=10,color='black',),
        customdata=[group['Nz'],group['TURN_RADIUS']],
        hovertemplate="Turn radius: %{customdata[1]:.0f} ft<br>"+\
                    "Nz: %{customdata[0]:.2f} g<br>" +\
                    "Turn Rate: %{y:.2f}°/sec<br>" +\
                    "TAS: %{x:.2f} kt<br>" + "<extra></extra>",
        showlegend=False,
        ))


    #plot requirements
    req_TAS=libs.atm.CAStoTAS(180,group_altitude,0,Offset=True)  #get the 180 KIAS in TAS
    req_Turn_Rate=np.rad2deg(libs.cst.G_IMPERIAL/(req_TAS*libs.cst.KT_TO_FPS)*np.tan(np.deg2rad(30))) #get the turn rate for 180 KIAS
    fig.add_trace(go.Scatter(x=[req_TAS],y=[req_Turn_Rate], name='Requirement', mode='markers', marker=dict(symbol='x',size=10,color='black',), showlegend=False,))


    #plot the turn radius and load factor contours
    fig.add_trace(go.Contour(x=x, y=y, z=Nz,
        contours=dict( showlines=True, showlabels=True, start=1.5, end=3, size=1, coloring='none',),
        line=dict(color='black', width=0.5,),
        showlegend=False,
        ))

    fig.add_trace(go.Contour(x=x, y=y, z=Nz,
        contours=dict( showlines=True, showlabels=True, start=1, end=7, size=1, coloring='none',),
        line=dict(color='black', width=1),
        showlegend=False,

        ))

    fig.add_trace(go.Contour(x=x, y=y, z=Nz,
        contours=dict( showlines=True, showlabels=True, start=3.17, end=3.17, size=1, coloring='none',labelformat="3.17 g structural limit"),
        line=dict(color='black', width=3),
        showlegend=False,
))

    fig.add_trace(go.Contour(
        x=x, y=y, z=TURN_RADIUS,
        contours=dict( showlines=True, showlabels=True, start=1000, end=5000, size=1000, coloring='none',),
        line=dict(color='black', dash='dash'),
        customdata=np.stack((Nz,TURN_RADIUS),axis=-1),
        hovertemplate="Turn radius: %{customdata[1]:.0f} ft<br>"+\
                    "Nz: %{customdata[0]:.2f} g<br>" +\
                    "Turn Rate: %{y:.2f}°/sec<br>" +\
                    "TAS: %{x:.2f} kt<br>" + "<extra></extra>",
        showlegend=False,
    ))

    #plot Vstall
    fig.add_trace(go.Scatter(x=Vstall_vect,y=Omega_vect,mode='lines',line=dict(color='black',width=3),showlegend=False,))

    #Plot Max TAS
    fig.add_trace(go.Scatter(x=[Vmo,Vmo],y=[0,Omega_Vmo],mode='lines+text',line=dict(color='black',width=3),showlegend=False,))
    fig.add_annotation(x=Vmo+2, y=Omega_Vmo/2,text='<b>Vmo</b>',showarrow=False,font=dict(size=16,),textangle=-90)
    Vstall_x=(Vstall+Vstall_maxg)/2
    Vstall_y=np.rad2deg(libs.cst.G_IMPERIAL/(Vstall_x*libs.cst.KT_TO_FPS)*np.sqrt((Vstall_x/Vstall_alt)**4-1))+1
    fig.add_annotation(x=Vstall_x, y=Vstall_y-0.5,text='<b>1.1 Vs</b>',showarrow=False,font=dict(size=16,),textangle=-35)

    struct_limit_x=(Vmo+Vstall_maxg)/2
    struct_limit_y=np.rad2deg(libs.cst.G_IMPERIAL/(struct_limit_x*libs.cst.KT_TO_FPS)*np.sqrt((Max_g)**2-1))+1
    fig.add_annotation(x=struct_limit_x, y=struct_limit_y-0.5,text='<b>Structural limit Vs</b>',showarrow=False,font=dict(size=16,),textangle=18)

    fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

    fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
        font=dict(size=16, color="black",family="Arial"),
        text=left_text,
        showarrow=False,)

    fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
        font=dict(size=16, color="black",family="Arial"),
        text=center_text,
        showarrow=False,)

    fig.show()
    fig.write_image("data/Perf/Level_turn.png", engine='kaleido')


## MOP 5 Descent performance

In [ ]:
#Data for FM descent
descent_data=pd.read_csv(r"data\Perf\master_FM_descent.csv")

ID=[0] #ID of the level accels in manual cruise climb from 5000 to 20000ft

#Flight manual data (to be updated based on the day conditions, mostly temperature)
Time_to_descend_20k=600 #in seconds (for ISA conditions and 11000 lb, 6.3 min to climb from 5000 to 20000ft)
Fuel_to_descend_20k=131-39 #in lb (for ISA conditions and 11000 lb, 100 lb to climb from 5000 to 20000ft)
Distance_to_descend_20k=64.5-15 #in nm (for ISA conditions and 11000 lb, 19 nm to climb from 5000 to 20000ft)

left_text="<b>Configuration:</b> Cruise<br><b>Calibrated airspeed:</b> 224 KIAS or MCP<br><b>Weight:</b> 12,050 lb<br><b>Rate of descent:</b> 1,500 ft/min<br>"
center_text="<b>Data basis:</b> Flight test<br><b>Test date:</b> April 25th, 2025<br><b>Tail number:</b> 76-00158<br><b>Temperature:</b> ISA+5°C<br>"

In [ ]:
filtered_data=descent_data[descent_data['ID'].isin(ID)]

fig=go.Figure()

fig = make_subplots(
    rows=3,
    cols=1,
    shared_xaxes=False,  # Optional: you can customize axes sharing
    shared_yaxes=False,  # We will be using individual y-axes for each plot
    vertical_spacing=0.15,
    subplot_titles=("Time to descend", "Fuel to descend", "Distance to descend"),  # Titles for each subplot
    # Define a secondary y-axis for each subplot
)



fig.update_layout(
    template=matlab_template,
    title="C-12C Flight Manual Descent (20,000 to 5,000 ft)",
    xaxis_title="Time (s)",
    xaxis=dict(range=[0, 605]),
    xaxis2_title="Fuel (lb)",
    xaxis3_title="Distance (Nm)",
    yaxis_title="Altitude (ft)",
    yaxis=dict(range=[0, 21000]),
    yaxis2_title="Altitude (ft)",
    yaxis2=dict(range=[0, 21000], showgrid=True),
    yaxis3_title="Altitude (ft)",
    yaxis3=dict(range=[0, 21000]),
    width=8.42*180,
    height=6.4*180,
    showlegend=False,

)

for id, group in filtered_data.groupby('ID'):
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black')),row=1, col=1)
    fig.add_trace(go.Scatter(x=group['Fuel'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black'),showlegend=False),row=2, col=1)
    fig.add_trace(go.Scatter(x=group['Distance'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black'),showlegend=False),row=3, col=1)

for annotation in fig['layout']['annotations']:
    annotation['font'] = dict(size=20, weight='bold')  # Set desired font size her

#Plot flight manual data
#Altitude
fig.add_trace(go.Scatter(x=[0,Time_to_descend_20k], y=[20000,5000],name="Flight manual",mode='lines+text',line=dict(color='black', dash='dash')), row=1, col=1)
fig.add_trace(go.Scatter(x=[0,Time_to_descend_20k*0.9], y=[20000,5000],name='+/-10%',mode='lines',line=dict(color='black', dash='dot')), row=1, col=1)
fig.add_trace(go.Scatter(x=[0,Time_to_descend_20k*1.1], y=[20000,5000],name='+10%', mode='lines',line=dict(color='black', dash='dot'), showlegend=False), row=1, col=1)

#Fuel
fig.add_trace(go.Scatter(x=[0,Fuel_to_descend_20k], y=[20000,5000],name="Flight manual",mode='lines',line=dict(color='black', dash='dash'), showlegend=False), row=2, col=1)
fig.add_trace(go.Scatter(x=[0,Fuel_to_descend_20k*0.9], y=[20000,5000],name='-10%',mode='lines',line=dict(color='black', dash='dot'), showlegend=False), row=2, col=1)
fig.add_trace(go.Scatter(x=[0,Fuel_to_descend_20k*1.1], y=[20000,5000],name='+10%',mode='lines',line=dict(color='black', dash='dot'), showlegend=False), row=2, col=1)

#Distance
fig.add_trace(go.Scatter(x=[0,Distance_to_descend_20k], y=[20000,5000],name="Flight manual", mode='lines',line=dict(color='black', dash='dash'), showlegend=False), row=3, col=1)
fig.add_trace(go.Scatter(x=[0,Distance_to_descend_20k*0.9], y=[20000,5000],name='-10%', mode='lines',line=dict(color='black', dash='dot'), showlegend=False),row=3, col=1)
fig.add_trace(go.Scatter(x=[0,Distance_to_descend_20k*1.1], y=[20000,5000],name='+10%',mode='lines',line=dict(color='black', dash='dot'), showlegend=False),row=3, col=1)

fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=left_text,
    showarrow=False,)

fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=center_text,
    showarrow=False,)

fig.show()
fig.write_image("data/Perf/FM_descent.png", engine='kaleido')

In [ ]:
#Data for Emergency descent
descent_data=pd.read_csv(r"data\Perf\master_emer_descent.csv")

ID=[0] #ID of the emergency descent

left_text="<b>Configuration:</b> Gear down, flaps 40%<br><b>Calibrated airspeed:</b> 170 KIAS<br><b>Power:</b> IDLE<br><b>Weight:</b> 11,200 lb<br>"
center_text="<b>Data basis:</b> Flight test<br><b>Test date:</b> April 22th, 2025<br><b>Tail number:</b> 76-00158<br><b>Temperature:</b> ISA<br>"

In [ ]:
filtered_data=descent_data[descent_data['ID'].isin(ID)]

fig=go.Figure()

fig = make_subplots(
    rows=3,
    cols=1,
    shared_xaxes=False,  # Optional: you can customize axes sharing
    shared_yaxes=False,  # We will be using individual y-axes for each plot
    vertical_spacing=0.15,
    subplot_titles=("Time to descend", "Fuel to descend", "Distance to descend"),  # Titles for each subplot
    # Define a secondary y-axis for each subplot
)

fig.update_layout(
    template=matlab_template,
    title="C-12C Flight Manual Descent (20,000 to 5,000 ft)",
    xaxis_title="Time (s)",
    xaxis=dict(range=[0, 220]),
    xaxis2_title="Fuel (lb)",
    xaxis3_title="Distance (Nm)",
    yaxis_title="Time to descend",
    yaxis=dict(range=[0, 21000]),
    yaxis2_title="Fuel to descend",
    yaxis2=dict(range=[0, 21000], showgrid=True),
    yaxis3_title="Distance to descend",
    yaxis3=dict(range=[0, 21000]),
    width=8.42*180,
    height=6.4*180,
    showlegend=False,
)

for id, group in filtered_data.groupby('ID'):
    fig.add_trace(go.Scatter(x=group['Time_rel'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black')),row=1, col=1)
    fig.add_trace(go.Scatter(x=group['Fuel'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black'),showlegend=False),row=2, col=1)
    fig.add_trace(go.Scatter(x=group['Distance'], y=group['GPS_ALT'], name=f'Climb {id}',line=dict(color='black'),showlegend=False),row=3, col=1)

for annotation in fig['layout']['annotations']:
    annotation['font'] = dict(size=20, weight='bold')  # Set desired font size her

fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=left_text,
    showarrow=False,)

fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=center_text,
    showarrow=False,)

fig.show()
fig.write_image("data/Perf/Emergency_descent.png", engine='kaleido')

## Bonus : flaps 40 Ps

In [ ]:
#Data SEP contour plot
accel_data=pd.read_csv(r"data\Perf\master_level_accel_40flap.csv")

left_text="<b>Configuration:</b> Approach (flaps 40%, gear down)<br><b>Power setting:</b> MCP<br><b>Temperature:</b> Test day<br>"
center_text="<b>Data basis:</b> Flight test<br><b>Test date:</b> April 8th, 2025 to May 25th, 2025<br><b>Tail number:</b> 73-01215 and 76-00158<br>"

In [ ]:
fig=go.Figure()

accel_data['FL']= ((accel_data['BARO_ALT'] / 500).round()*5 ).astype(int) #rescale to similar than speed
accel_data['TAS_rounded']= accel_data['CAS'].round().astype(int)

x=np.linspace(100, 280, 181)
y=np.linspace(70, 200, 27)
X, Y = np.meshgrid(x, y)
z = np.full((len(y), len(x)), np.nan)  # initialize with NaNs
for i in range(len(y)):
    for j in range(len(x)):
        z[i,j]=accel_data.loc[(accel_data['FL']==y[i]) & (accel_data['TAS_rounded']==x[j]),'Ps_fit'].mean()


# 1️⃣ Interpolate missing (NaN) values using griddata
# Step 1: Get known points
x_known, y_known = np.meshgrid(x, y)
points_known = np.column_stack((x_known[~np.isnan(z)], y_known[~np.isnan(z)]))
values_known = z[~np.isnan(z)]

# Step 2: Create full grid
points_full = np.column_stack((X.ravel(), Y.ravel()))

# Step 3: Interpolate
z_interp = griddata(points_known, values_known, points_full, method='cubic', rescale=True)
z_interp = z_interp.reshape(z.shape)

# 2️⃣ Optional: Smooth the result using Gaussian filter
# z_smooth = gaussian_filter(z_interp, sigma=3)

fig.add_trace(go.Contour(
    x=x,
    y=y*100,
    z=z_interp,
    colorscale='YlOrRd',
    colorbar=dict(title='Specific Excess Power (ft/s)', thickness=20, tickfont=dict(size=14, family='Arial')),
    line=dict(color='black',width=2),
    contours=dict(
        showlines=True,
        showlabels=True,
        labelfont=dict(size=16,color='black',weight='bold'),
        start=0,
        size=10,
        end=60,
        ),
    contours_coloring='none',
    ))


x=np.linspace(0, 280, 281)
y=np.zeros(len(x))

for i in range(0,25000,2000):
    for j in range(len(x)):
        y[j]=i-1/(2*32.2)*(libs.atm.CAStoTAS(x[j],i,0,Offset=True)*1.68781)**2

    if i%10000==0:
        dash='dash'
        width=1
    else:
        dash='dash'
        width=1
    fig.add_trace(go.Scatter(x=x,y=y,line=dict(dash=dash, color='black', width=width)))

fig.update_layout(template=matlab_template,
        title="C-12C Climb Schedule",
        xaxis=dict(title='Calibrated Airspeed (kt)',range=[100,180]),
        yaxis=dict(title='Pressure Altitude (ft)', range=[7000,15000]),
        showlegend=False,
        width=8.42*180,
        height=6.4*180,
        )

fig.add_shape(type="rect", xref="paper", yref="paper",
            x0=0, y0=1.05,     # Bottom-left corner
            x1=1, y1=1.15,     # Top-right corner
            line=dict(color="black", width=1,),
            layer="below",
        )

fig.add_annotation(x=0, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=left_text,
    showarrow=False,)

fig.add_annotation(x=0.55, y=1.15, xref="paper", yref="paper",align='left',
    font=dict(size=16, color="black",family="Arial"),
    text=center_text,
    showarrow=False,)

fig.show()